In [1]:
import xarray as xr
import subprocess
from datetime import datetime

def log(msg):
    print(f"[{datetime.now().strftime('%Y-%m-%d %H:%M:%S')}] {msg}")

In [3]:
cmd_pet = [
    "/home/users/fmaussion/.miniforge3/envs/spei/bin/process_climate_indices",
    "--index", "pet",
    "--periodicity", "monthly",
    "--netcdf_temp", "tmp_era_tas.nc",
    "--var_name_temp", "t2m",
    "--output_file_base", "tmp_era",
    "--multiprocessing", "all",
]

cmd_spei = [
    "/home/users/fmaussion/.miniforge3/envs/spei/bin/process_climate_indices",
    "--index", "spei",
    "--periodicity", "monthly",
    "--netcdf_precip", "tmp_era_pr.nc",
    "--var_name_precip", "tp",
    "--netcdf_pet", "tmp_era_pet_thornthwaite.nc",
    "--var_name_pet", "pet_thornthwaite",
    "--output_file_base", "tmp_era",
    "--scales", "3", "6", "12", "24",
    "--calibration_start_year", "1981",
    "--calibration_end_year", "2010",
    "--multiprocessing", "all",
]

In [7]:
cdir = '/home/users/fmaussion/www_fmaussion/teaching/qcr/'
RESs = ['ERA5_UltraLowRes', 'ERA5_LowRes'] 
SPEIS = ["3", "6", "12", "24"]


log("=== START SPEI PROCESSING ===")
log(f"RESs = {RESs}, SPEIS = {SPEIS}")
print()

for res in RESs:
    log(f"---- Resolution: {res} ----")

    f_tas =  f'{cdir}/{res}/{res}_Monthly_t2m.nc'
    f_pr =   f'{cdir}/{res}/{res}_Monthly_tp.nc'
    of_pet = f'{cdir}/{res}/{res}_Monthly_pet.nc'
    of_spei = f'{cdir}/{res}/{res}_Monthly_spei.nc'

    log(f"Input TAS: {f_tas}")
    log(f"Input PR:  {f_pr}")
    log(f"Output PET: {of_pet}")
    log(f"Output SPEI: {of_spei}")

    # -----------------------------------------------------------
    # PREPARE TAS
    # -----------------------------------------------------------
    log("Reading TAS → tmp_era_tas.nc ...")
    with xr.open_dataset(f_tas) as ds:
        save_lat = ds['latitude']
        save_enc_tas = ds['t2m'].encoding
        ds = ds.rename({'latitude':'lat', 'longitude':'lon'})
        ds['lat'] = ds['lat'].clip(-90+0.00001, 90-0.000001)
        ds['t2m'] = ds['t2m'].transpose('lat', 'lon', 'time')
        ds.to_netcdf('tmp_era_tas.nc')
    log("Wrote tmp_era_tas.nc")

    log("Running PET computation ...")
    try:
        subprocess.run(cmd_pet, check=True, capture_output=True)
    except subprocess.CalledProcessError as e:
        log("ERROR: PET computation failed!")
        log(e.stderr.decode())
        raise
    log("PET finished.")

    # -----------------------------------------------------------
    # PREPARE PR
    # -----------------------------------------------------------
    log("Reading PR → tmp_era_pr.nc ...")
    with xr.open_dataset(f_pr) as ds:
        ds['time'] = ds.time.dt.floor('D')        
        save_lat = ds['latitude']
        save_enc_pr = ds['tp'].encoding
        ds = ds.rename({'latitude':'lat', 'longitude':'lon'})
        ds['lat'] = ds['lat'].clip(-90+0.00001, 90-0.000001)
        ds['tp'] = ds['tp'].transpose('lat', 'lon', 'time') * ds['time.days_in_month'] * 1000 
        ds['tp'].attrs['units'] = 'mm'
        ds.to_netcdf('tmp_era_pr.nc')
    log("Wrote tmp_era_pr.nc")

    log("Running SPEI computation ...")
    try:
        subprocess.run(cmd_spei, check=True, capture_output=True)
    except subprocess.CalledProcessError as e:
        log("ERROR: PET computation failed!")
        log(e.stderr.decode())
        raise
    log("SPEI finished.")

    # -----------------------------------------------------------
    # SAVE PET
    # -----------------------------------------------------------
    log("Writing final PET file ...")
    with xr.open_dataset('tmp_era_pet_thornthwaite.nc') as ds:
        ds = ds.load()
        ds['pet_thornthwaite'] = ds['pet_thornthwaite'].transpose('time', 'lat', 'lon')
        ds = ds.rename({'lat':'latitude', 'lon':'longitude'})
        ds['latitude'] = save_lat
        
        for key in ['source', 'szip', 'zstd', 'bzip2', 'blosc', 'coordinates', 'preferred_chunks']:
            save_enc_tas.pop(key, None)
            
        enc = {'pet_thornthwaite': save_enc_tas}
        ds.to_netcdf(of_pet, encoding=enc)

    log(f"Saved PET → {of_pet}")

    # -----------------------------------------------------------
    # SAVE SPEI
    # -----------------------------------------------------------
    log("Writing final SPEI file ...")

    for key in ['source', 'szip', 'zstd', 'bzip2', 'blosc', 'coordinates', 'preferred_chunks']:
        save_enc_pr.pop(key, None)

    enc = {}
    varname = f'spei_pearson_{int(SPEIS[0]):02d}'

    log(f"Reading SPEI {SPEIS[0]} ...")
    with xr.open_dataset(f'tmp_era_{varname}.nc') as ds:
        ds = ds.load()
        ds[varname] = ds[varname].transpose('time', 'lat', 'lon')
        ds = ds.rename({'lat':'latitude', 'lon':'longitude'})
        ds['latitude'] = save_lat
        enc[varname] = save_enc_pr

    # Add others if any
    for spei in SPEIS[1:]:
        varname = f'spei_pearson_{int(spei):02d}'
        log(f"Reading additional SPEI {spei} ...")

        with xr.open_dataset(f'tmp_era_{varname}.nc') as tds:
            tds = tds.load()
            tds[varname] = tds[varname].transpose('time', 'lat', 'lon')
            tds = tds.rename({'lat':'latitude', 'lon':'longitude'})
            tds['latitude'] = save_lat
            ds[varname] = tds[varname]
            enc[varname] = save_enc_pr
    
    ds.to_netcdf(of_spei, encoding=enc)
    log(f"Saved SPEI → {of_spei}")

log("=== ALL DONE ===")

[2025-11-27 14:11:27] === START SPEI PROCESSING ===
[2025-11-27 14:11:27] RESs = ['ERA5_UltraLowRes', 'ERA5_LowRes'], SPEIS = ['3', '6', '12', '24']

[2025-11-27 14:11:27] ---- Resolution: ERA5_UltraLowRes ----
[2025-11-27 14:11:27] Input TAS: /home/users/fmaussion/www_fmaussion/teaching/qcr//ERA5_UltraLowRes/ERA5_UltraLowRes_Monthly_t2m.nc
[2025-11-27 14:11:27] Input PR:  /home/users/fmaussion/www_fmaussion/teaching/qcr//ERA5_UltraLowRes/ERA5_UltraLowRes_Monthly_tp.nc
[2025-11-27 14:11:27] Output PET: /home/users/fmaussion/www_fmaussion/teaching/qcr//ERA5_UltraLowRes/ERA5_UltraLowRes_Monthly_pet.nc
[2025-11-27 14:11:27] Output SPEI: /home/users/fmaussion/www_fmaussion/teaching/qcr//ERA5_UltraLowRes/ERA5_UltraLowRes_Monthly_spei.nc
[2025-11-27 14:11:27] Reading TAS → tmp_era_tas.nc ...
[2025-11-27 14:11:29] Wrote tmp_era_tas.nc
[2025-11-27 14:11:29] Running PET computation ...
[2025-11-27 14:11:37] PET finished.
[2025-11-27 14:11:37] Reading PR → tmp_era_pr.nc ...
[2025-11-27 14:11:37]

In [8]:
'done'

'done'